# Loading Data Using Dask

This user guide notebook demonstrates how to load unstructured grid datasets in UXarray using Dask.  

In [1]:
import uxarray as ux
from dask.distributed import Client, LocalCluster
import xarray as xr

## Dask Setup

This notebook is executed on a single node of NCAR Derecho's Supercomputer within a JupyterHub instance. 

In [2]:
cluster = LocalCluster()
client = Client(cluster)
client

<Client: 'tcp://127.0.0.1:45077' processes=16 threads=256, memory=235.00 GiB>

## Data

This notebook uses two datasets to demonstrate Dask functionality.

The first dataset is a 3.75 km MPAS Atmosphere Grid paired with a single diagnostic file.

The second dataset is from the Department of Energy (DOE) Energy Exascale Earth System Model (E3SM). The case is set up as follows:

- Atmosphere-only (AMIP)
- Present-day control forcing (F2010)
- 1-degree horizontal resolution (ne30pg2)
- Sea surface temperatures and sea ice set to deftion needed]

Special thanks to Falko Judt (NSF NCAR MMM) and Rachel Tam (UIUC) for sharing the data with us!


In [3]:
mpas_grid_path = "/glade/campaign/cisl/vast/uxarray/data/dyamond/3.75km/grid.nc"
mpas_data_path = "/glade/campaign/mmm/wmr/fjudt/projects/dyamond_1/3.75km/diag.2016-08-01_00.00.00.nc"

In [4]:
e3sm_grid_path = (
    "/glade/campaign/cisl/vast/uxarray/data/e3sm_keeling/E3SM_grid/ne30pg2_grd.nc"
)
e3sm_data_pattern = "/glade/campaign/cisl/vast/uxarray/data/e3sm_keeling/ENSO_ctl_1std/unstructured/*.nc"

## Loading Large Grid Files Since UXarray represents every grid format in the UGRID conventions, multiple pre-processing steps are often applied to the original grid data to ensure compliance with our conventions. Most commonly, these steps include:

- Converting from 1-indexed to 0-indexed connectivity variables
- Replacing existing fill values with our standardized `INT_FILL_VALUE`
- Shifting longitude coordinates to the range [-180, 180]

Many of these operations are relatively simple and can be delayed until the variable is needed. By loading the data as Dask arrays instead of directly into memory, we can delay these computations while still creating a `Grid` instance. An added benefit is that only the variables required are computed when accessed, which is useful since grid files often contain additional variables that may not be immediately needed.

Let's examine an extreme case. Below, we have a complete 3.75 km MPAS atmosphere grid that contains a full set of grid variables, including multiple coordinates and connectivity variables.

First, let's try to eagerly load the entire grid into memory without specifying any chunking.


In [39]:
%%time
uxgrid = ux.open_grid(mpas_grid_path)
uxgrid

None
CPU times: user 14.1 s, sys: 1min 32s, total: 1min 46s
Wall time: 1min 39s


<uxarray.Grid>
Original Grid Type: MPAS
Grid Dimensions:
  * n_node: 83886080
  * n_edge: 125829120
  * n_face: 41943042
  * n_max_face_nodes: 6
  * n_max_face_edges: 6
  * n_max_face_faces: 6
  * n_max_node_faces: 3
  * two: 2
Grid Coordinates (Spherical):
  * node_lon: (83886080,)
  * node_lat: (83886080,)
  * edge_lon: (125829120,)
  * edge_lat: (125829120,)
  * face_lon: (41943042,)
  * face_lat: (41943042,)
Grid Coordinates (Cartesian):
  * node_x: (83886080,)
  * node_y: (83886080,)
  * node_z: (83886080,)
  * edge_x: (125829120,)
  * edge_y: (125829120,)
  * edge_z: (125829120,)
  * face_x: (41943042,)
  * face_y: (41943042,)
  * face_z: (41943042,)
Grid Connectivity Variables:
  * face_face_connectivity: (41943042, 6)
  * edge_face_connectivity: (125829120, 2)
  * edge_node_connectivity: (125829120, 2)
  * node_face_connectivity: (83886080, 3)
  * face_node_connectivity: (41943042, 6)
  * face_edge_connectivity: (41943042, 6)
Grid Descriptor Variables:
  * face_areas: (41943042,)
  * edge_face_distances: (125829120,)
  * edge_node_distances: (125829120,)

This takes over a minute on a node of Derecho. We can observe that our `Grid` contains a large number of variables, many of which we may never end up using.

Compared to using Xarray directly, this represents a significant difference in performance. Note that because UXarray requires all grids to be internally represented using UGRID conventions, loading a `Grid` will always be slower than a pure Xarray approach.


In [6]:
%%time
xrds = xr.open_dataset(mpas_grid_path)

CPU times: user 106 ms, sys: 159 ms, total: 265 ms
Wall time: 1.04 s


One workaround is to specify a `chunks` parameter, which uses Dask to load the grid. Since Dask allows computations to be delayed, we can defer these computations until necessary, significantly reducing the time required to open a grid and explore its contents.

Below, we specify `chunks=-1`, which instructs us to load all of our data as Dask arrays, with a single chunk per variable.


In [7]:
%%time
uxgrid = ux.open_grid(mpas_grid_path, chunks=-1)
uxgrid

-1
CPU times: user 874 ms, sys: 488 ms, total: 1.36 s
Wall time: 14.2 s


<uxarray.Grid>
Original Grid Type: MPAS
Grid Dimensions:
  * n_node: 83886080
  * n_edge: 125829120
  * n_face: 41943042
  * n_max_face_nodes: 6
  * n_max_face_edges: 6
  * n_max_face_faces: 6
  * n_max_node_faces: 3
  * two: 2
Grid Coordinates (Spherical):
  * node_lon: (83886080,)
  * node_lat: (83886080,)
  * edge_lon: (125829120,)
  * edge_lat: (125829120,)
  * face_lon: (41943042,)
  * face_lat: (41943042,)
Grid Coordinates (Cartesian):
  * node_x: (83886080,)
  * node_y: (83886080,)
  * node_z: (83886080,)
  * edge_x: (125829120,)
  * edge_y: (125829120,)
  * edge_z: (125829120,)
  * face_x: (41943042,)
  * face_y: (41943042,)
  * face_z: (41943042,)
Grid Connectivity Variables:
  * face_node_connectivity: (41943042, 6)
  * edge_face_connectivity: (125829120, 2)
  * node_face_connectivity: (83886080, 3)
  * edge_node_connectivity: (125829120, 2)
  * face_edge_connectivity: (41943042, 6)
  * face_face_connectivity: (41943042, 6)
Grid Descriptor Variables:
  * face_areas: (41943042,)
  * edge_face_distances: (125829120,)
  * edge_node_distances: (125829120,)

We can see above that all our variables are loaded as `dask.array` objects. If we inspect the high-level Dask graph for `face_node_connectivity`, we can observe all the computations and steps taken to parse and encode the data according to the UGRID conventions.


In [8]:
uxgrid.face_node_connectivity.data.dask

HighLevelGraph with 17 layers.
<dask.highlevelgraph.HighLevelGraph object at 0x14d0b639df10>
 0. original-open_dataset-verticesOnCell-bf7a984439bb267dd3463be0321be53d
 1. open_dataset-verticesOnCell-bf7a984439bb267dd3463be0321be53d
 2. astype-c92bc80ebc54956fcc28078df192a41f
 3. original-open_dataset-nEdgesOnCell-acc252cd4d77eb187160b7314ab2a543
 4. open_dataset-nEdgesOnCell-acc252cd4d77eb187160b7314ab2a543
 5. astype-fbdcb7f49fdae873ba694bac7fc48701
 6. getitem-149ca190fe8db177a5211959d67d7ee1
 7. array-2a2bc8dce6a9b78455d5fb439011f414
 8. greater_equal-2d1a7a47fd227551905b779fce997c1f
 9. invert-9f8a3423432fa8a6c044a6077f651ab6
 10. transpose-27a470fc1f21f1ecf2b93e74b2929b02
 11. where-8d58b872c1ad4b269110802d019c6040
 12. ne-5373f6ebc9c1a1bad77b4422984d3ec4
 13. where-674faff89656f343b9d92ed9352dd276
 14. sub-2e8e6ffdaeb8aca6261d37bc892ec282
 15. ne-0f992b881c4b11dd6dd37e20b682661f
 16. where-220ec0d25750ec28efbf84f9a4cf39bb

If we want to load this variable into memory, we can use the `.load()` or `.compute()` methods:
- `.load()` performs an in-place loading.
- `.compute()` returns a new variable with the data loaded into memory.

For example, to load the `face_node_connectivity` variable into memory, we would do the following:

In [9]:
uxgrid.face_node_connectivity.load()
uxgrid.face_node_connectivity

<xarray.DataArray 'face_node_connectivity' (n_face: 41943042,
                                            n_max_face_nodes: 6)> Size: 2GB
array([[                   2,                    0,                   64,
                          66,                   65,                    1],
       [                  64,                    0,                   16,
                          32,                   48, -9223372036854775808],
       [                   0,                    2,                    3,
                          17,                   18,                   16],
       ...,
       [            83886069,             83886065,             83886066,
                    83886067,             83886071,             83886070],
       [            83886074,             83886068,             83886069,
                    83886070,             83886076,             83886075],
       [            83886076,             83886070,             83886071,
                    83886072,             83886078,             83886077]])
Dimensions without coordinates: n_face, n_max_face_nodes
Attributes:
    cf_role:      face_node_connectivity
    long name:    Maps every face to its corner nodes.
    start_index:  0
    _FillValue:   -9223372036854775808

If you wanted to use ``.compute()`` instead, below is an example on our ``node_lon`` variable. 

Below we showcase how to load the `node_lon` variable into memory using `.compute()`:

In [10]:
uxgrid.node_lon = uxgrid.node_lon.compute()
uxgrid.node_lon

<xarray.DataArray 'node_lon' (n_node: 83886080)> Size: 336MB
array([ 89.98285 ,  89.93793 ,  89.97223 , ..., -20.905151, -20.925049,
       -20.934937], dtype=float32)
Dimensions without coordinates: n_node

Inspecting our `Grid` once again, we can see that after performing these computations, only the `node_lon` and `face_node_connectivity` variables are loaded into memory, while the remaining variables still exist as Dask arrays.


In [35]:
uxgrid

<uxarray.Grid>
Original Grid Type: MPAS
Grid Dimensions:
  * n_node: 83886080
  * n_edge: 125829120
  * n_face: 41943042
  * n_max_face_nodes: 6
  * n_max_face_edges: 6
  * n_max_face_faces: 6
  * n_max_node_faces: 3
  * two: 2
Grid Coordinates (Spherical):
  * node_lon: (83886080,)
  * node_lat: (83886080,)
  * edge_lon: (125829120,)
  * edge_lat: (125829120,)
  * face_lon: (41943042,)
  * face_lat: (41943042,)
Grid Coordinates (Cartesian):
  * node_x: (83886080,)
  * node_y: (83886080,)
  * node_z: (83886080,)
  * edge_x: (125829120,)
  * edge_y: (125829120,)
  * edge_z: (125829120,)
  * face_x: (41943042,)
  * face_y: (41943042,)
  * face_z: (41943042,)
Grid Connectivity Variables:
  * face_face_connectivity: (41943042, 6)
  * edge_face_connectivity: (125829120, 2)
  * edge_node_connectivity: (125829120, 2)
  * node_face_connectivity: (83886080, 3)
  * face_node_connectivity: (41943042, 6)
  * face_edge_connectivity: (41943042, 6)
Grid Descriptor Variables:
  * face_areas: (41943042,)
  * edge_face_distances: (125829120,)
  * edge_node_distances: (125829120,)

TODO: Add markdown about which grid formats support "lazy" conversions to UGRID

## Loading Large Datasets

The previous example focused solely on working with the unstructured grid definition. However, in most cases, you will have an unstructured grid paired with data. This may include loading a large series of data variables from a climate model, with many spatial and temporal dimensions. For these applications, using Dask is highly encouraged since most machines can't load all of this data into memory.
.


### Continuation of MPAS Example

Using the samgridet as above, we can pair it with a data file to create a `ux.UxDataset`. In this example, we have a high-resolution grid paired with a single diagnostic file from MPAS. In this case, we can set `chunks=-1` if we simply want our data to be loaded as Dask array.


In [13]:
%%time
uxds = ux.open_dataset(mpas_grid_path, mpas_data_path, chunks=-1)
uxds

None
CPU times: user 1.74 s, sys: 675 ms, total: 2.42 s
Wall time: 13.9 s


<xarray.UxDataset> Size: 17GB
Dimensions:             (time: 1, StrLen: 64, n_face: 41943042, n_node: 83886080)
Coordinates:
  * time                (time) datetime64[ns] 8B 2016-08-01
Dimensions without coordinates: StrLen, n_face, n_node
Data variables: (12/99)
    xtime_old           (time, StrLen) |S1 64B dask.array<chunksize=(1, 64), meta=np.ndarray>
    taux                (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    tauy                (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    olrtoa              (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    cldcvr              (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    vert_int_qv         (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    ...                  ...
    umeridional_300hPa  (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    umeridional_400hPa  (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    uzonal_300hPa       (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    uzonal_400hPa       (time, n_face) float32 168MB dask.array<chunksize=(1, 41943042), meta=np.ndarray>
    xtime               (time, StrLen) |S1 64B dask.array<chunksize=(1, 64), meta=np.ndarray>
    zgrid               (n_face) float32 168MB dask.array<chunksize=(41943042,), meta=np.ndarray>

### E3SM Example

There may be times where the grid you are working with is small enough to where the grid is small enough and you want to directly load it into memory, but there may other temporal or spatial dimensions that you would like to chunk across in a dataset. You can specify the `chunk_grid=False` parameter to declare thisfunctionality.


In [8]:
%%time
uxds = ux.open_mfdataset(
    e3sm_grid_path,
    e3sm_data_pattern,
    chunks={
        "lev": 4,
        "time": 4,
    },
    chunk_grid=False,
)
uxds

None
CPU times: user 26.2 s, sys: 1.53 s, total: 27.7 s
Wall time: 21.9 s


<xarray.UxDataset> Size: 37GB
Dimensions:              (time: 72, n_face: 21600, lev: 72, ilev: 73,
                          cosp_prs: 7, nbnd: 2, cosp_tau: 7, cosp_ht: 40,
                          cosp_sr: 15, cosp_htmisr: 16, cosp_tau_modis: 7,
                          cosp_reffice: 6, cosp_reffliq: 6, cosp_sza: 5,
                          cosp_scol: 10)
Coordinates: (12/13)
  * lev                  (lev) float64 576B 0.1238 0.1828 0.2699 ... 993.8 998.5
  * ilev                 (ilev) float64 584B 0.1 0.1477 0.218 ... 997.0 1e+03
  * cosp_prs             (cosp_prs) float64 56B 9e+04 7.4e+04 ... 2.45e+04 9e+03
  * cosp_tau             (cosp_tau) float64 56B 0.15 0.8 2.45 ... 41.5 100.0
  * cosp_scol            (cosp_scol) int32 40B 1 2 3 4 5 6 7 8 9 10
  * cosp_ht              (cosp_ht) float64 320B 1.896e+04 1.848e+04 ... 240.0
    ...                   ...
  * cosp_sza             (cosp_sza) float64 40B 0.0 20.0 40.0 60.0 80.0
  * cosp_htmisr          (cosp_htmisr) float64 128B 0.0 250.0 ... 1.8e+04
  * cosp_tau_modis       (cosp_tau_modis) float64 56B 0.15 0.8 ... 41.5 100.0
  * cosp_reffice         (cosp_reffice) float64 48B 5e-06 1.5e-05 ... 7.5e-05
  * cosp_reffliq         (cosp_reffliq) float64 48B 4e-06 9e-06 ... 2.5e-05
  * time                 (time) object 576B 0001-02-01 00:00:00 ... 0007-01-0...
Dimensions without coordinates: n_face, nbnd
Data variables: (12/471)
    lat                  (time, n_face) float64 12MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    lon                  (time, n_face) float64 12MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    area                 (time, n_face) float64 12MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    hyam                 (time, lev) float64 41kB dask.array<chunksize=(1, 72), meta=np.ndarray>
    hybm                 (time, lev) float64 41kB dask.array<chunksize=(1, 72), meta=np.ndarray>
    P0                   (time) float64 576B 1e+05 1e+05 1e+05 ... 1e+05 1e+05
    ...                   ...
    soa_c1DDF            (time, n_face) float32 6MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c1SFWET          (time, n_face) float32 6MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c2DDF            (time, n_face) float32 6MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c2SFWET          (time, n_face) float32 6MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c3DDF            (time, n_face) float32 6MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c3SFWET          (time, n_face) float32 6MB dask.array<chunksize=(1, 21600), meta=np.ndarray>

The `parallel=True` parameter can be used to perform the open and preprocess steps in parallel using `dask.delayed`. By default, this parameter is set to `False`.

In [16]:
%%time
uxds = ux.open_mfdataset(
    e3sm_grid_path,
    e3sm_data_pattern,
    chunks={"time": 4, "lev": 4},
    chunk_grid=False,
    parallel=True,
)
uxds

None
CPU times: user 20.4 s, sys: 1.26 s, total: 21.6 s
Wall time: 18.9 s


<xarray.UxDataset> Size: 37GB
Dimensions:              (time: 72, n_face: 21600, lev: 72, ilev: 73,
                          cosp_prs: 7, nbnd: 2, cosp_tau: 7, cosp_ht: 40,
                          cosp_sr: 15, cosp_htmisr: 16, cosp_tau_modis: 7,
                          cosp_reffice: 6, cosp_reffliq: 6, cosp_sza: 5,
                          cosp_scol: 10)
Coordinates: (12/13)
  * lev                  (lev) float64 576B 0.1238 0.1828 0.2699 ... 993.8 998.5
  * ilev                 (ilev) float64 584B 0.1 0.1477 0.218 ... 997.0 1e+03
  * cosp_prs             (cosp_prs) float64 56B 9e+04 7.4e+04 ... 2.45e+04 9e+03
  * cosp_tau             (cosp_tau) float64 56B 0.15 0.8 2.45 ... 41.5 100.0
  * cosp_scol            (cosp_scol) int32 40B 1 2 3 4 5 6 7 8 9 10
  * cosp_ht              (cosp_ht) float64 320B 1.896e+04 1.848e+04 ... 240.0
    ...                   ...
  * cosp_sza             (cosp_sza) float64 40B 0.0 20.0 40.0 60.0 80.0
  * cosp_htmisr          (cosp_htmisr) float64 128B 0.0 250.0 ... 1.8e+04
  * cosp_tau_modis       (cosp_tau_modis) float64 56B 0.15 0.8 ... 41.5 100.0
  * cosp_reffice         (cosp_reffice) float64 48B 5e-06 1.5e-05 ... 7.5e-05
  * cosp_reffliq         (cosp_reffliq) float64 48B 4e-06 9e-06 ... 2.5e-05
  * time                 (time) object 576B 0001-02-01 00:00:00 ... 0007-01-0...
Dimensions without coordinates: n_face, nbnd
Data variables: (12/471)
    lat                  (time, n_face) float64 12MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    lon                  (time, n_face) float64 12MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    area                 (time, n_face) float64 12MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    hyam                 (time, lev) float64 41kB dask.array<chunksize=(1, 72), meta=np.ndarray>
    hybm                 (time, lev) float64 41kB dask.array<chunksize=(1, 72), meta=np.ndarray>
    P0                   (time) float64 576B 1e+05 1e+05 1e+05 ... 1e+05 1e+05
    ...                   ...
    soa_c1DDF            (time, n_face) float32 6MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c1SFWET          (time, n_face) float32 6MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c2DDF            (time, n_face) float32 6MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c2SFWET          (time, n_face) float32 6MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c3DDF            (time, n_face) float32 6MB dask.array<chunksize=(1, 21600), meta=np.ndarray>
    soa_c3SFWET          (time, n_face) float32 6MB dask.array<chunksize=(1, 21600), meta=np.ndarray>

In [32]:
xrds = xr.open_mfdataset(
    e3sm_data_pattern,
    chunks={"time": 4, "lev": -1, "cols": -1},
    concat_dim="time",
    combine="nested",
)

In [36]:
xrds.Q.dims

('time', 'lev', 'ncol')

In [23]:
xrds.Q.dims

('time', 'lev', 'ncol')

While the performance difference isn't huge, you will typically experience better performance by setting `parallel=True`.


Moving on, we can investigate one of the data arrays in the loaded dataset

By calling one of the variables `Q` - specific humidity, we can look at the data array dimensions. The full data array has 1 point in time, 72 vertical levels, and a total of 21600 faces in the simulation grid, corresponding to the single monthly we loaded and the info shown below: `time: 1, lev: 72, n_face: 21600`. 

We declared a chunk size of 4 for both the time and level dimensions. We can see this in our "72 chunks in 145 graph layers" output, 

The chunk size is also shown in the second line, where they contain 4 vertical levels instead of 72 (see `chunksize=(1,4,21600)`), proving we have successfully chunked the data.

In [20]:
uxds.Q.data

dask.array<concatenate, shape=(72, 72, 21600), dtype=float32, chunksize=(1, 72, 21600), chunktype=numpy.ndarray>

When working with dask, walays remember to shutdown your client!

In [6]:
client.shutdown()